In [ ]:
spark = %adb_spark add \
    --spark-conf spark.adb.eni.vswitchId= <your_vswitch_id> \
    --spark-conf spark.adb.eni.securityGroupId= <your_security_group_id>\
    --spark-conf spark.adb.acuPerApp=16\
    --resource-group <your_job_resource_group_name>

Initializing ADB Spark Connector Server
Creating new Spark Connector Server...
Submitting Spark connector server:amv-wz99icf7v3831i7i with config: {"file": "local:///opt/spark/jars/offline-sql.jar", "name": "SparkConnectorServer", "className": "com.aliyun.adb.spark.connectServer.ADBSparkConnectServer", "conf": {"spark.adb.version": "3.5", "spark.adb.uiMeta.enabled": "false", "spark.adb.eni.enabled": "true", "spark.sql.hive.metastore.version": "adb", "spark.adb.eni.vswitchId": "vsw-wz926zcxi9g55ji6or73e", "spark.adb.eni.securityGroupId": "sg-wz909my4jibz0o2wr1kg", "spark.adb.acuPerApp": "16"}}


Submitted Spark connector server ID: s202511101606sz8f1a30a0003020
Waiting for Spark Connect Server to start... s202511101606sz8f1a30a0003020->SUBMITTED
Waiting for Spark Connect Server to start... s202511101606sz8f1a30a0003020->RUNNING
Spark Connect Server started at host: 172.25.219.62
ADB Spark status:RUNNING, AppId:s202511101606sz8f1a30a0003020, Web UI:https://adbsparkui-cn-shenzhen.aliyuncs.com/?token=eyJqb2JpZCI6InMyMDI1MTExMDE2MDZzejhmMWEzMGEwMDAzMDIwLTAwMDEiLCJleHBpcmVzIjoxNzYyNzY1NjMzOTk4LCJuYW1lc3BhY2UiOiJhbXYtd3o5OWljZjd2MzgzMWk3aS1zcGFyayIsInZjbmFtZSI6IlNlY29uZEpvYlJlc291cmNlR3JvdXAiLCJ1c2VyIjoiMTU3NzYyMzcxMTgyNzk3NiIsInNpZ25hdHVyZSI6IjMwMDZjNzNkOGNmNjRiMDgwODU2N2E1OGJmN2VmMmQ3NmIwYmYzNzJhOGQwNDQwZTliYTlmMTllOTQ5N2ZjNzNhODZiNjU0ZWI0NTE4YzZlM2Q2OWFjZDQ1MDY1ZmNjOTM4MWZjZDA5MzQ3MjVhNTUwMmI4N2VhZTY1YTg0YzVmMjZhMWVmYTIxOTc0YTU5ZTkyODczNzc3ZDBkMWUyMzZhZjhhZDE0MGMxODEyZDM2MWNlNmIyZjVmNjcwNGQ4MzJlNTA0Njk2Y2I5YmMyZDFkYWFhMWYxMmY0YTQxMjY2MWE3M2FlZGViNTYwNzY3NzhlYjFmNDNkMTIyYzZiZWRhNT

In [2]:
import time
batch_start_datetime = time.strftime('%Y-%m-%d %H:%M:%S', time.localtime(time.time()))
print(batch_start_datetime)

2025-11-10 16:07:24


In [ ]:
CREATE DATABASE IF NOT EXISTS db_lake LOCATION 'oss://aliyun-oa-adb-spark-1577623711827976-oss-cn-shenzhen/db_lake/'

DataFrame[]

In [ ]:
from pyspark.sql.functions import  current_timestamp
import random
import string
import random
import time
from datetime import datetime, timedelta

def generate_enhanced_order_data(num_orders=9000,batch_start_datetime=None):
    """Generate complete order transaction data including product ID and category"""
    # 1. Predefined product categories and weights (simulating the distribution of real e-commerce platforms)
    categories = [
        "Electronics",      
        "Clothing",        
        "Books",            
        "Home & Kitchen",   
        "Sports",           
        "Beauty",           
        "Toys",             
        "Grocery",          
        "Health",           
        "Automotive"        
    ]
    
    # Category weight (simulating actual sales share)
    category_weights = [
        25,  # Electronics 25%
        20,  # Clothing 20%
        15,  # Books 15%
        12,  # Home & Kitchen 12%
        8,   # Sports 8%
        7,   # Beauty 7%
        5,   # Toys 5%
        4,   # Grocery 4%
        3,   # Health 3%
        1    # Automotive 1%
    ]
    
    # 2. Pre-generate 1000 product IDs (simulating a real product library)
    product_ids = []
    for i in range(1, 1001):
        # Product ID format: CAT-XXXX (category abbreviation + 4-digit serial number)
        category_code = categories[(i-1) % len(categories)][:3].upper()
        product_ids.append(f"{category_code}-{i:04d}")
    
    # 3. Create a mapping from product ID to category (to ensure data consistency)
    product_catalog = {}
    for pid in product_ids:
        # Extract category code to determine the main category
        cat_code = pid[:3]
        if cat_code == "ELE":
            category = "Electronics"
        elif cat_code == "CLO":
            category = "Clothing"
        elif cat_code == "BOO":
            category = "Books"
        elif cat_code == "HOM":
            category = "Home & Kitchen"
        elif cat_code == "SPO":
            category = "Sports"
        elif cat_code == "BEA":
            category = "Beauty"
        elif cat_code == "TOY":
            category = "Toys"
        elif cat_code == "GRO":
            category = "Grocery"
        elif cat_code == "HEA":
            category = "Health"
        else:  # AUT
            category = "Automotive"
        
        product_catalog[pid] = category

    # 4. Base timeframe (last 30 days)
    end_time = datetime.now()
    start_time = end_time - timedelta(days=30)
    
    # 5. Generate order data
    orders = []
    for i in range(1, num_orders + 1):
        user_id = f"U{random.randint(1000, 9999)}"
        order_id = i
        product_id = random.choice(product_ids)        
        product_category = product_catalog[product_id]        
        product_name = f"Name_{''.join(random.choices('0123456789abcdefg', k=20))}"        
        if product_category == "Electronics":
            amount = round(random.uniform(200.0, 5000.0), 2)
        elif product_category == "Clothing":
            amount = round(random.uniform(30.0, 300.0), 2)
        elif product_category == "Books":
            amount = round(random.uniform(10.0, 100.0), 2)
        elif product_category == "Home & Kitchen":
            amount = round(random.uniform(50.0, 800.0), 2)
        elif product_category == "Sports":
            amount = round(random.uniform(100.0, 1500.0), 2)
        else:
            amount = round(random.uniform(5.0, 500.0), 2)        
        time_offset = random.randint(0, int((end_time - start_time).total_seconds()))
        transaction_time = start_time + timedelta(seconds=time_offset)
        transaction_time_str = transaction_time.strftime('%Y-%m-%d %H:%M:%S')        
        orders.append((
            user_id,
            order_id,
            product_id,
            product_category,
            product_name,
            amount,
            transaction_time_str,
            batch_start_datetime
        ))
    
    return orders


df = generate_enhanced_order_data(10000,batch_start_datetime)
schema = ['user_id', 'order_id', 'product_id', 'product_category', 'product_name', 'amount', 'transaction_time','batch_start_datetime']
df = spark.createDataFrame(df, schema)
df.write \
    .format("delta") \
    .mode("append") \
    .option("mergeSchema", "true")\
    .saveAsTable('db_lake.orders_raw')
print("task done")

task done


In [ ]:
select * from db_lake.orders_raw limit 100;

DataFrame[user_id: string, order_id: bigint, product_id: string, product_category: string, product_name: string, amount: double, transaction_time: string, batch_start_datetime: string]

In [ ]:
describe history db_lake.orders_raw

DataFrame[version: bigint, timestamp: timestamp, userId: string, userName: string, operation: string, operationParameters: map<string,string>, job: struct<jobId:string,jobName:string,jobRunId:string,runId:string,jobOwnerId:string,triggerType:string>, notebook: struct<notebookId:string>, clusterId: string, readVersion: bigint, isolationLevel: string, isBlindAppend: boolean, operationMetrics: map<string,string>, userMetadata: string, engineInfo: string]

In [ ]:
select count(*) from db_lake.orders_raw

DataFrame[count(1): bigint]